In [1]:
%matplotlib widget 
import matplotlib.pyplot as plt
import hyperspy.api as hs
from sklearn.cluster import DBSCAN
from skimage import filters
import numpy as np
from skimage.morphology import dilation
from skimage.morphology import disk
import os
import py4DSTEM
print(py4DSTEM.__file__)
print(py4DSTEM.__version__)
# py4DSTEM.utils.configuration_checker.check_cupy_gpu(True)
# py4DSTEM.utils.check_config()

import h5py
from py4DSTEM.visualize import show
import sys, io
sys.path.append('/dls/science/groups/e02/Mohsen/code/Git_Repos/epsic_tools')
import epsic_tools.api as epsic

### Logging set-up
def console_handler(stream='stdout'):
    """
    Create a handler for logging to the original console.
    """
    assert stream in {'stdout', 'stderr'}, "stream must be one of 'stdin' or 'stdout'"
    # Get the file handle of the original std stream.
    fh = getattr(sys, stream)._original_stdstream_copy
    # Create a writable IO stream.
    stream = io.TextIOWrapper(io.FileIO(fh, 'w'))
    # Set up a stream handler.
    return logging.StreamHandler(stream)

import logging

logger = logging.getLogger('myLogger')
logger.setLevel(logging.DEBUG)
logger.addHandler(console_handler())

logger.debug(f"py4DSTEM.__file__ is {py4DSTEM.__file__}")
logger.debug(f"py4DSTEM.__version__ is {py4DSTEM.__version__}")


/dls_sw/apps/python/miniforge/4.10.0-0/envs/epsic3.10/lib/python3.10/site-packages/py4DSTEM/__init__.py
0.14.8
Checking Module Dependencies
 All Dependencies for Base are Installed 
 All Dependencies for Ipyparallel are Installed 
 Not All Dependencies for Cuda are Installed
 All Dependencies for Acom are Installed 
 Not All Dependencies for Aiml are Installed
 Not All Dependencies for Aiml-cuda are Installed
 All Dependencies for Numba are Installed 


DEBUG:myLogger:py4DSTEM.__file__ is /dls_sw/apps/python/miniforge/4.10.0-0/envs/epsic3.10/lib/python3.10/site-packages/py4DSTEM/__init__.py
DEBUG:myLogger:py4DSTEM.__version__ is 0.14.8



fill_cross=1 
crop_q=130
raw_data_path=/dls/e02/data/2023/mg34931-2/processing/Merlin/FA_50pct_3/20230724_141239/20230724_141239.hdf5
v_min=0.01
v_max=0.1
synthetic_probe=1
syn_probe_rad=3
syn_probe_width=3
probe_path=
hot_pix_thresh=2
load_prepared_data=0
prepared_data_path=
save_path_name=
cif_file1_path=/dls/e02/data/2023/mg34931-2/processing/notebooks/FAPbI3_mod_simple.cif
cif_file2_path=/dls/science/groups/e02/Mohsen/code/jupyterhub_active/user_visits_notebooks/mg34931-2_Jihoo/cif_files/p4mbm.cif
corr_factor=1.1

In [ ]:
# Keep Empty!



# Calibration values

In [ ]:
# Thse values to be transferred from a au-xgrating calibration analysis

pixel_size_inv_Ang = 0.00947646 
probe_step_size_Ang = 190  
p_ellipse = (246.10879816058716,
 241.16983307697623,
 76.93620460418315,
 74.78092080404805,
 -2.6543567689014544)



# Prepare data

In [ ]:
root_path = os.path.dirname(raw_data_path)
print(root_path) 
logger.debug(f'root path is: {root_path}')
save_path = os.path.join(root_path, save_path_name)
logger.debug(f'saving path is: {save_path}')
if not os.path.exists(save_path):
    os.mkdir(save_path)

time_stamp = os.path.basename(raw_data_path).split('.')[0]
print(time_stamp)

In [ ]:
if load_prepared_data == '0':
    d = hs.load(raw_data_path, reader='HSPY')
    logger.debug(f'raw dataset shape after loading is: {d.data.shape}')
    
    if fill_cross == '1':
        d_cross_rm = map(epsic.warp_3d.remove_cross, d.data)
        d_cross_rm = list(d_cross_rm)
        d = hs.signals.Signal2D(d_cross_rm)
        d_mean = d.mean()
    else:
        d_mean = d.mean()
    
    v_min = float(v_min) # 0.01
    v_max = float(v_max) # 0.99
    probe_semiangle, qx0, qy0 = py4DSTEM.process.calibration.origin.get_probe_size(d_mean.data, v_min,v_max)
    
    if crop_q != '':
        crop_q = int(crop_q)
        d = d.isig[int(qx0 - crop_q):int(qx0 + crop_q), int(qy0 - crop_q):int(qy0 + crop_q)]
        logger.debug(f'cropped data to: {d.data.shape}')
    if len(d.data.shape) == 3:
        
        s1 = int(np.floor(d.data.shape[0]**0.5))
        s2 = d.data.shape[0]//s1
        s3, s4 = d.data.shape[1], d.data.shape[2]
        d = hs.signals.Signal2D(d.data.reshape((s1,s2,s3,s4)))
        d = d.inav[:-1,:]
        # binning by 2
        # d = d.inav[1:,1:].rebin(scale=(2,2,1,1))
    # Save data
    prepared_data_path = os.path.join(save_path, f'{time_stamp}_prepared_data.h5')
    py4DSTEM.io.save(prepared_data_path, d.data, mode = 'o')

# Reload data to Py4DSTEM

In [ ]:

dataset = py4DSTEM.read(prepared_data_path)



In [ ]:
dataset = py4DSTEM.DataCube(dataset.data)


In [ ]:
# Diffraction space
dataset.calibration.set_Q_pixel_size(pixel_size_inv_Ang)
dataset.calibration.set_Q_pixel_units('A^-1')


# Real space
dataset.calibration.set_R_pixel_size(probe_step_size_Ang)
dataset.calibration.set_R_pixel_units('A')

In [ ]:
# Check masking
hot_pix_thresh = float(hot_pix_thresh)
dataset, mask = dataset.filter_hot_pixels(thresh = hot_pix_thresh, return_mask=True)


In [ ]:
plt.figure()
plt.imshow(mask)

In [ ]:
fig = plt.gcf()
fig.savefig(os.path.join(save_path, 'hot_pix_mask.png'))
logger.debug(f'dataset shape is: {dataset.shape}')

In [ ]:
dataset.get_dp_max();
dataset.get_dp_mean();


In [ ]:
fig, ax = py4DSTEM.show([
        dataset.tree('dp_mean'), 
        dataset.tree('dp_max'), 
        # dataset_probe.tree('dp_mean'),
    ],
    cmap='inferno',
    power = 0.5,
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'dp_mean_max.PNG'))

In [ ]:
# Create an annular dark field (ADF) virtual detector using user-chosen values:
center = (dataset.shape[-1]//2,dataset.shape[-1]//2)
radii = (15,75)

# Plot the ADF detector
py4DSTEM.visualize.show(
    dataset.tree('dp_max'), 
    scaling='log',
    annulus = {
      'center':center,
      'radii':radii,
      'alpha':0.3,
      'fill':True
    }
)

# Calculate the ADF image
dataset.get_virtual_image(
    mode = 'annulus',
    geometry = ((center),radii),
    name = 'dark_field',
)

# Plot the ADF image
py4DSTEM.visualize.show(
    dataset.tree('dark_field'),
)

In [ ]:
# Choose some diffraction patterns to use for hyperparameter tuning

rxs = 50,50,50,60,60,60
rys = 25,35,45,25,35,120
colors=['r','c','r','c','r','c']

py4DSTEM.visualize.show_points(
    dataset.tree('dark_field'),
    x=rxs,
    y=rys,
    pointcolor=colors,
    figsize=(8,8)
)

In [ ]:
# Try making a synthetic probe
syn_probe_rad = int(syn_probe_rad)
syn_probe_width = float(syn_probe_width)

syn_probe = py4DSTEM.braggvectors.probe.Probe.generate_synthetic_probe(syn_probe_rad, syn_probe_width, (dataset.data.shape[-1], dataset.data.shape[-1]))

In [ ]:
plt.figure()
plt.imshow(syn_probe.data[0, : ,: ])
plt.savefig(os.path.join(save_path,'synthetic_probe.PNG'))

In [ ]:
# Construct a probe template to use as a kernel for correlation disk detection
probe_semiangle = syn_probe_rad
syn_probe_kernel = syn_probe.get_kernel(
    mode = 'sigmoid',
    radii = (probe_semiangle * 0.5, probe_semiangle * 3.0),
    bilinear=True,
)

# Plot the probe kernel
fig, ax = py4DSTEM.visualize.show_kernel(
    syn_probe.kernel, 
    R=20, 
    L=20, 
    W=1,
    figsize = (8,4),
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'probe_kernel.PNG'))



In [ ]:
# Test hyperparameters on a few probe positions
# Visualize the diffraction patterns and the located disk positions

# Hyperparameters
detect_params = {
    'corrPower': 1.0, 
    'sigma': 0,
    'edgeBoundary': 2,
    'minRelativeIntensity': 0.0,
    'minAbsoluteIntensity': 1.3, 
    'minPeakSpacing': 2,
    'subpixel' : 'poly',
    'upsample_factor': 8,
    'maxNumPeaks': 1000,
    'CUDA': True,
}

disks_selected = dataset.find_Bragg_disks(
    data = (rxs, rys),
    template=syn_probe_kernel,
    **detect_params,
)


fig, ax = py4DSTEM.visualize.show_image_grid(
    get_ar = lambda i:dataset.data[rxs[i],rys[i],:,:],
    H=2, 
    W=3,
    axsize=(4,4),
    get_bordercolor = lambda i:colors[i],
    get_x = lambda i: disks_selected[i].data['qx'],
    get_y = lambda i: disks_selected[i].data['qy'],
    get_pointcolors = lambda i: colors[i],
    open_circles = True,
    scale = 200,
    intensity_range = 'absolute',
    vmin = 5,
    vmax = 70,
    returnfig=True,
)


fig.savefig(os.path.join(save_path,'peak_finding_test.PNG'))

In [ ]:
bragg_peaks = dataset.find_Bragg_disks(
    template = syn_probe_kernel,
    **detect_params,
)

In [ ]:
# compute
bvm = bragg_peaks.histogram( mode='raw' )

# show
show(bvm)

In [ ]:
dataset.calibration

In [ ]:
bragg_peaks.setcal()

In [ ]:
bragg_peaks.calstate

In [ ]:
# First, generate a mask of the beamstop, plot it
dataset.get_beamstop_mask(
    threshold = 0.1,
    distance_edge = 7,
    # include_edges=False,
);
py4DSTEM.show(
    dataset.tree("mask_beamstop"),
    intensity_range='absolute',
    vmin=0,
    vmax=1,
    figsize = (4,4),
)

In [ ]:
# Apply the mask to the raw bragg peaks
bragg_peaks_masked = bragg_peaks.mask_in_Q(
    dataset.tree("mask_beamstop").data,
)
# Create a bragg vector map (2D histogram of all detected bragg peaks) for both raw and masked Bragg peaks
bragg_vector_map = bragg_peaks.get_bvm(mode='raw')
bragg_vector_map_masked = bragg_peaks_masked.get_bvm(mode='raw')
# Plot a comparison image between the original and masked bragg vector map
fig, ax = py4DSTEM.show(
    [
        bragg_vector_map,
        bragg_vector_map_masked,
    ],
    combine_images = True,
    figsize = (4,4),
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'bragg_peaks_masked.PNG'))

In [ ]:
# Measure the origin
center_guess = (139.5,130.5)
# radial_range = (8,200)
qx0_meas,qy0_meas,mask_meas = bragg_peaks_masked.measure_origin(
    center_guess=center_guess,
    score_method='distance',
    # findcenter='max',
)

fig, ax = show(
    [qx0_meas,qy0_meas],
    cmap = 'RdBu',
    mask = mask_meas,
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'bragg_peaks_masked_measure_origin.PNG'))

In [ ]:
# Fit a plane to the origins

qx0_fit,qy0_fit,qx0_residuals,qy0_residuals = bragg_peaks_masked.fit_origin(
    robust= True,
    robust_thresh= 1.2,
)

In [ ]:
fig = plt.gcf()
fig.savefig(os.path.join(save_path, 'BF_disc_align.png'))


In [ ]:
logger.debug(f"Calibration state: {bragg_peaks_masked.calibration}")

In [ ]:
bragg_peaks_masked.calstate

In [ ]:
# Now that we've calibrated the center positions, we can re-compute
# the Bragg vector map, this time with the center correction applied

sampling = 2

# compute
bvm = bragg_peaks_masked.histogram(
    #mode='cal',             # 'cal' is the default mode, so this line can be included or left out
    sampling = sampling,
)

# show
# overlay a circle around the center for visualization purposes
fig, ax = show(
    bvm,
    circle={
        'center' : bvm.origin,   # the centered BVM knows where its origin is 
        'R' : 4*sampling,
        'fill' : False,
        'linewidth' : 1
    },
    returnfig = True,
    #vmax=0.9
)
fig.savefig(os.path.join(save_path, 'BF_disc_align_bvm.png'))

In [ ]:
# Compare this to the uncalibrated BVM - much better!

# compute raw vs. centered
bvm_r = bragg_peaks_masked.histogram( mode='raw', sampling=sampling )
bvm_c = bragg_peaks_masked.histogram( mode='cal', sampling=sampling )

# show
show( [bvm_r, bvm_c] ,vmax=0.99)

# show, zooming in on origin
L = 20
x,y = bvm_c.origin
import numpy as np
x0,xf = np.round([x-L,x+L]).astype(int)
y0,yf = np.round([y-L,y+L]).astype(int)

show(
    [
    bvm_r[x0:xf,y0:yf],
    bvm_c[x0:xf,y0:yf]
    ],
    vmax=0.9
)

In [ ]:
fig = plt.gcf()
fig.savefig(os.path.join(save_path, 'BF_disc_align_before_after.png'))

In [ ]:
bragg_peaks_masked.calibration.set_p_ellipse(p_ellipse)

In [ ]:
logger.debug(f"Calibration state: {bragg_peaks_masked.calibration}")

In [ ]:
bragg_peaks_masked.calstate

### ACOM from here

In [ ]:
# load crystals
crystal1 = py4DSTEM.process.diffraction.Crystal.from_CIF(cif_file1_path)
logger.debug(f"Loading this CIF: {cif_file1_path}")
crystal2 = py4DSTEM.process.diffraction.Crystal.from_CIF(cif_file2_path)
logger.debug(f"Loading this CIF: {cif_file2_path}")




In [ ]:
# Calculate structure factors
k_max = 1.5

crystal1.calculate_structure_factors(k_max)
crystal2.calculate_structure_factors(k_max)



# Compare measured diffraction pattern with reference crystal structure
crystal1.plot_scattering_intensity(
    bragg_peaks = bragg_peaks_masked,
    bragg_k_power = 2.0,
)

In [ ]:
# Display the current pixel size
print('   Initial pixel size = ' + \
    str(np.round(bragg_peaks_masked.calibration.get_Q_pixel_size(),8)) + \
    ' ' + bragg_peaks_masked.calibration.get_Q_pixel_units())



In [ ]:

# Save calibrated Bragg peaks
filepath_braggdisks_cali = os.path.join(save_path, 'braggdisks_masked.h5')
py4DSTEM.save(
    filepath_braggdisks_cali,
    bragg_peaks_masked,
    mode='o',
)

In [ ]:
fig, ax = crystal1.plot_scattering_intensity(
    bragg_peaks = bragg_peaks_masked,
    bragg_k_power = 2.0,
    figsize = (12,2),
    k_min=0.1,
    k_max=1.0,
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'compare_crstal1_to_sim_powder_pattern.png'))
fig, ax = crystal2.plot_scattering_intensity(
    bragg_peaks = bragg_peaks_masked,
    bragg_k_power = 2.0,
    figsize = (12,2),
    k_min=0.1,
    k_max=1.0,
    returnfig=True,
)
fig.savefig(os.path.join(save_path,'compare_crstal2_to_sim_powder_pattern.png'))


In [ ]:
# Create orientation plans 

# Create orientation plans 
acom_params = {
    'zone_axis_range': 'auto',
    'angle_step_zone_axis': 2.0,
    'angle_step_in_plane': 2.0,
    'accel_voltage': 300e3,
    'corr_kernel_size': 0.08,
#     'tol_peak_delete': 0.04,
    'intensity_power': 0.125,
#     'intensity_power': 0.0,
    'CUDA': True,
}


crystal1.orientation_plan(**acom_params)
crystal2.orientation_plan(**acom_params)

In [ ]:
# Test matching on some probe positions
sigma_compare = 0.02  # 0.01 Excitation error for the simulated diffraction patterns
figsize = (12,7)

xind, yind = 25, 25
xind, yind = 40, 60
xind, yind = 60, 60

# plotting parameters
plot_params = {
    'scale_markers': 2000,
    'scale_markers_compare': 40,
    'plot_range_kx_ky': crystal1.k_max,
    'min_marker_size': 2,
    'add_labels': False,
}

# Find best fit orientations
orientation1  = crystal1.match_single_pattern(
    bragg_peaks_masked.cal[xind,yind],
    num_matches_return = 1,
    verbose = True,
)
orientation2  = crystal2.match_single_pattern(
    bragg_peaks_masked.cal[xind,yind],
    num_matches_return = 1,
    verbose = True,
)

# Simulated bragg peaks from best fit orientations
peaks_fit_1 = crystal1.generate_diffraction_pattern(
    orientation1,
    sigma_excitation_error=sigma_compare)
peaks_fit_2 = crystal2.generate_diffraction_pattern(
    orientation2,
    sigma_excitation_error=sigma_compare)

# plot comparisons
fig,ax = plt.subplots(1,2,figsize=figsize)

py4DSTEM.process.diffraction.plot_diffraction_pattern(
    peaks_fit_1,
    bragg_peaks_compare=bragg_peaks_masked.cal[xind,yind],
    **plot_params,
    input_fig_handle=(fig,[ax[0]]),
)
py4DSTEM.process.diffraction.plot_diffraction_pattern(
    peaks_fit_2,
    bragg_peaks_compare=bragg_peaks_masked.cal[xind,yind],
    **plot_params,
    input_fig_handle=(fig,[ax[1]]),
)
fig.savefig(os.path.join(save_path, 'testing_ACOM.PNG'))

In [ ]:
# Fit orientation to all probe positions
orientation_map_1 = crystal1.match_orientations(
    bragg_peaks_masked,
    num_matches_return = 1,
    min_number_peaks = 5,
)
orientation_map_2 = crystal2.match_orientations(
    bragg_peaks_masked,
    num_matches_return = 1,
    min_number_peaks = 5,
)

In [ ]:
# plot orientation map
images_orientation_1, fig, ax = crystal1.plot_orientation_maps(
    orientation_map_1,
    corr_range = np.array([1,3]),
    corr_normalize = False,
    camera_dist = 10,
    show_axes = False,
    figsize = (12,3),
    returnfig = True,
)

fig.savefig(os.path.join(save_path,'ACOM_Full_crystal1.png'))

In [ ]:


images_orientation_2, fig, ax = crystal2.plot_orientation_maps(
    orientation_map_2,
    corr_range = np.array([1,3]),
    corr_normalize = False,
    camera_dist = 10,
    show_axes = False,
    figsize = (12,3),
    returnfig = True,
)

fig.savefig(os.path.join(save_path,'ACOM_Full_crystal2.png'))

In [ ]:
crystal1.save_ang_file(
    file_name=os.path.join(save_path,'orientation_map_crystal1.ang'),
    orientation_map = orientation_map_1)

crystal2.save_ang_file(
    file_name=os.path.join(save_path,'orientation_map_crystal2.ang'),
    orientation_map = orientation_map_2)

In [ ]:
corr_factor = float(corr_factor) # 1.1
mask_phase_two = orientation_map_2.corr[:,:,0] > corr_factor * orientation_map_1.corr[:,:,0]

np.save(os.path.join(save_path,'hexagonal_patterns.npy'), 
        mask_phase_two)

fig, ax =py4DSTEM.show(
    mask_phase_two,
    returnfig = True,
)
fig.savefig(os.path.join(save_path,'hexagonal_patterns.png'))